# shubnikov de haas oscillations analysis




#### python libraries and notes
* https://plotly.com/python/

* https://github.com/fbeilstein/machine_learning


## reading and pre processing data

We start with importing data from csv. Data was saved as **(field,T ; voltave, V)**.

Function **readSdh** reads from the csv and creates useful columns. 

In [79]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

#plotting libraries
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots 

import scipy as sp
from scipy import fftpack





def readSdH(csvName, current): #function to read and preprocess sdH oscillations 
    df = pd.read_csv(csvName, header=None)
    df.columns = ['field', 'voltage']

    df['resistance']= df['voltage']/current
    df['1/B'] = 1/df['field']
    df['dR/R'] = (df['resistance']-df['resistance'][0])/df['resistance'][0]
    
    return df

#data4K =readSdH('data/sdH4K.csv',50* 10**(-9))
#data10K =readSdH('data/sdH10K.csv',100* 10**(-9))

mesa4K =readSdH('data/sdh/mesa4K.csv',50* 10**(-9))
mesa6K =readSdH('data/sdh/mesa6K.csv',100* 10**(-9))
mesa10K =readSdH('data/sdh/mesa10K.csv',100* 10**(-9))
mesa15K =readSdH('data/sdh/mesa15K.csv',100* 10**(-9))
mesa20K =readSdH('data/sdh/mesa20K.csv',100* 10**(-9))



#defining columns for relative resistance oscillations and 1/B field
#data4K['dR/R'] = (data4K['resistance']-data4K['resistance'][0])/data4K['resistance'][0]
#data10K['dR/R'] = (data10K['resistance']-data10K['resistance'][0])/data10K['resistance'][0]


### plotting the oscillations

In [80]:
fig = go.Figure()

fig.add_trace(go.Scatter(
    x = mesa4K['field'], y = mesa4K['dR/R'],
    name="4K"       # this sets its legend entry
))

fig.add_trace(go.Scatter(
    x = mesa6K['field'], y = mesa6K['dR/R'],
    name="6K"
))

fig.add_trace(go.Scatter(
    x = mesa10K['field'], y = mesa10K['dR/R'],
    name="10K"
))

fig.add_trace(go.Scatter(
    x = mesa15K['field'], y = mesa15K['dR/R'],
    name="15K"
))

fig.add_trace(go.Scatter(
    x = mesa20K['field'], y = mesa20K['dR/R'],
    name="20K"
))


fig.update_layout(height=800, width=1000,template = 'simple_white', title_text="Stacked Subplots")
fig.update_layout(
    title=r'Mesa sdH oscillations',
    xaxis_title=r'Magnetic field, T',
    yaxis_title=r'$\frac{R_i-R(0)}{R(0)}$', font=dict(
        size=20
    )
)
fig.update_layout(legend_orientation="h")

fig.show()




## Filtering data

as we are mainly interested in oscillationg signal, we can pass all of our data through a high pass filter to get rid of static background.  


- https://www.youtube.com/watch?v=s2K1JfNR7Sc&t=339s
- https://www.youtube.com/watch?v=wJgBB4EsUHw&t=36s
- https://www.youtube.com/watch?v=dmzikG1jZpU


### resampling

FIRST, we will resample our data so the points are uniformly distributed. 

solution from here https://stackoverflow.com/questions/41493282/in-python-pandas-how-can-i-re-sample-and-interpolate-a-dataframe

In [213]:

#will create new dataframes so that the old ones are not corrupted. might create memory problems. keep in mind

def reSampleSdH(df, field1, field2, number_of_points):

    #mesa4K.set_index('date', inplace=True)
    indexList = np.linspace(field1, field2, number_of_points+1)
    df1 = df.set_index('field')
    df1 = df1.loc[~df1.index.duplicated(keep='first')]
    df1 = df1.drop_duplicates()
    df1 = df1.reindex(df1.index.union(indexList), copy = False).interpolate('index')
    df1 = df1.reindex(index=indexList) 
    df1 = df1.drop(df1.index[0])
    df1.index.name = 'field'
    return df1

samplerate = 5000

mesa4Kresampled = reSampleSdH(mesa4K, 0, 10, samplerate)
mesa6Kresampled = reSampleSdH(mesa6K, 0, 10, samplerate)
mesa10Kresampled = reSampleSdH(mesa10K, 0, 10, samplerate)
mesa15Kresampled = reSampleSdH(mesa15K, 0, 10, samplerate)
mesa20Kresampled = reSampleSdH(mesa20K, 0, 10, samplerate)



def plotSdH(df): 
    fig = px.scatter(df, y = df['dR/R'], width = 600, height = 400, template = 'simple_white')
    fig.update_layout(
    xaxis_title=r'Magnetic field, T',
    yaxis_title=r'$\frac{R_i-R(0)}{R(0)}$', font=dict(
        size=15
    ))
#markers style
    fig.update_traces(marker=dict(size=3,opacity=0.8, color = "#7AC5CD",
                              line=dict(width=1,
                                        color="#53868B")),
                  selector=dict(mode='markers'))
    fig.show()


plotSdH(mesa4Kresampled)

### get the spectrum of the data
with the data uniformly distributed we can use FFT algorithms to cut off extremely low frequencies.


https://stackoverflow.com/questions/19122157/fft-bandpass-filter-in-python



In [246]:
from scipy.fft import fft
from scipy.fftpack import rfft, irfft, fftfreq
# Number of sample points
def spectrumB(df, maxfreq):
    N = df.shape[0] #number of elements
    T = df.index.values[3]-df.index.values[2]
    timepoints = np.linspace(0.0, N*T, N)
    data = df['dR/R'].values
    yf = fft(data)
    freq = fftfreq(data.size, d=T)
#    freq = np.linspace(0.0, 1.0/(2.0*T), N//2)
    yAbs = 2.0/N * np.abs(yf[0:N//2])
   
    fig = px.line(x= freq[:maxfreq], y = yAbs[:maxfreq], width = 600, height = 400, template = 'simple_white')    
    fig.update_layout(
    xaxis_title=r'1/Magnetic field, 1/T',
    yaxis_title=r'Amplitude', font=dict(
        size=18
    ))
#markers style
    fig.update_traces(marker=dict(size=2,opacity=1, color = "black",
                              line=dict(width=.5,
                                        color="#53868B")),
                  selector=dict(mode='markers'))
    fig.show() 
    
    f_signal = irfft(data)
    cut_f_signal = f_signal.copy()
#    cut_f_signal[(freq > 5)] = 0

    cut_signal = irfft(cut_f_signal)
    

    fig = px.line(x= timepoints, y = cut_signal, width = 600, height = 400, template = 'simple_white')
    fig.show()

    
    
spectrumB(mesa4Kresampled,100)



## Getting $k_\text{F}$ from SdH oscillations

Here we define $f$ as the frequency of oscillations over $1/B$. 

The frequencies of the quantum oscillations of resistance $f$ are related to the cross section of the Fermi surfaces $A_{\text{k}}$ in the $k_{\parallel}$ plane by the Onsager relation:

$f = \frac{h}{4 \pi^2 e} A_{\text{k}} = \frac{h}{4 \pi e} k_{\parallel} ^2$


*Note*: we use almost free electron model, therefore, we consider Fermi surface to be a sphere. The section of the sphere is a circle. That means that $A_{\text{k}} = \pi k^2$.


First, we are getting the frequency by performing FFT on resistance oscillations over $1/B$


In [192]:
#plot inputs 


def plot1OverB(df):

    df = df.loc[df['1/B'] <.35] 
    #insetDF = df.loc[(df['1/B'] >= insetA) & (df['1/B'] <= insetB)]
    
    fig = px.scatter(mesa4K, x = df['1/B'], y = df['dR/R'], width = 800, height = 400, template = 'simple_white')
    fig.update_layout(
        xaxis_title=r'1/B, 1/T',
        yaxis_title=r'$\frac{R_i-R(0)}{R(0)}$', font=dict(
        size=16
    ))
    #markers style
    fig.update_traces(marker=dict(size=3,opacity=1, color = "black",
                              line=dict(width=.5,
                                        color="#53868B")),
                  selector=dict(mode='markers'))
    fig.show()
    
plot1OverB(mesa4K)
print('Mesa 4K')
plot1OverB(mesa6K)
print('Mesa 6K')
plot1OverB(mesa10K)
print('Mesa 10K')
plot1OverB(mesa15K)
print('Mesa 15K')
plot1OverB(mesa20K)
print('Mesa 20K')


Mesa 4K


Mesa 6K


Mesa 10K


Mesa 15K


Mesa 20K


### non uniform FFT

the issue with our data is that it is not evenly spaced in terms of 1/B (because the sweep is spaced in terms of B). I didn't want to work with the library so I am trying to write a function for 'irregular fourier transform'that just accounts for the time stamps. (https://mathematica.stackexchange.com/questions/110064/how-to-realize-a-fourier-transform-on-a-non-uniform-sampling-data this example worked in mathemtica).

here we define fft as the following:

$X(f_k)=\frac{\sum_{n=0}^{N-1} x_{n} e^{-2 \pi i t_{n} f_{k}}}{N}, \quad 0 \leq k \leq M$


unfortunately, right now it is VERY slow. need to fix that ASAP. There are different non uniform Fast Fourier Transform algorithms. Need to take a look


#### useful tutorials 
- what Fourier transform is https://www.youtube.com/watch?v=spUNpyF58BY
- what fast fourier transform is https://www.youtube.com/watch?v=E8HeD-MUrjY


In [96]:
#input for a function -- (dataset_Name, starting_freq, end_freq, step (be careful, changes computation speed dramatically))

def ift(df, f1, f2, step):
    dfInt = df.loc[df['1/B'] <.5] 
    n = dfInt.shape[0] #number of points in 'time'
    freq = np.arange(f1, f2, step) #create a set of frequencies
    vals = dfInt['dR/R'].values #values in our fft transform
    times = dfInt['1/B'].values #'times' in our fft transform
    transform = np.zeros(len(freq),dtype=complex)
    #df['freq'] = freq
    df.loc[:,'freq'] = pd.Series(freq)  #this helps avoiding creating additional data structure. however, the rows don't make much sense anymore. unlucky :(
    for i in range(len(freq)):
        transform[i] = sum(vals[k]*np.exp(-2j*times[k]*np.pi*freq[i]) for k in range(n))/n
    
    df.loc[:,'transform'] = pd.Series(np.absolute(transform))
  
    fig = px.scatter(x=freq, y=np.absolute(transform),width = 1000, height = 800, template = 'simple_white')
    fig.update_layout(
    xaxis_title=r'Magnetic field, T',
    yaxis_title=r'Amplitude', font=dict(
        size=18
    ))
#markers style
    fig.update_traces(marker=dict(size=2,opacity=1, color = "black",
                              line=dict(width=.5,
                                        color="#53868B")),
                  selector=dict(mode='markers'))
    fig.update_layout(yaxis_type="log")
    fig.show()


    

In [97]:
dft4K = ift(mesa4K,1,300, 0.1)
print('dft 4K mesa')


dft 4K mesa


In [85]:
dft6K = ift(mesa6K,1,300,.1)
print('dft 6K mesa')


dft 6K mesa


In [86]:
dft10K = ift(mesa10K,1,300,.1)
print('dft 10K mesa')

dft 10K mesa


In [16]:
dft15K = ift(mesa15K,1,300,.1)
print('dft 15K mesa')

dft 15K mesa


In [17]:
dft20K = ift(mesa20K,1,300,.1)
print('dft 10K mesa')

dft 10K mesa


### extracting the frequency from the fft

In [116]:

#this returns the maximum frequency of the DFT
frequency4K = mesa4K.loc[mesa4K['transform'].idxmax()][5]
print('4K frequency is %f Hz' % frequency4K)

frequency6K = mesa10K.loc[mesa6K['transform'].idxmax()][5]
print('10K frequency is %f Hz' % frequency6K)

frequency10K = mesa10K.loc[mesa10K['transform'].idxmax()][5]
print('10K frequency is %f Hz' % frequency10K)

#frequency15K = mesa15K.loc[mesa15K['transform'].idxmax()][5]
#print('10K frequency is %f Hz' % frequency15K)

#frequency20K = mesa20K.loc[mesa20K['transform'].idxmax()][5]
#print('10K frequency is %f Hz' % frequency20K)


import scipy.constants 
 

kf4K = np.sqrt(2*scipy.constants.e*frequency4K/scipy.constants.hbar)
print('4K kFermi is %.3E m^-2' %kf4K)    
kf6K = np.sqrt(2*scipy.constants.e*frequency6K/scipy.constants.hbar)
print('6K kFermi is %.3E m^-2' %kf6K)
kf10K = np.sqrt(2*scipy.constants.e*frequency10K/scipy.constants.hbar)
print('10K kFermi is %.3E m^-2' %kf10K)


4K frequency is 128.000000 Hz
10K frequency is 127.900000 Hz
10K frequency is 127.800000 Hz
4K kFermi is 6.236E+08 m^-2
6K kFermi is 6.234E+08 m^-2
10K kFermi is 6.232E+08 m^-2


## comparing $k_f$ with Hall measurements

we know that from Hall coefficient is linked to the $n_s$ as:

$ R_H = \frac{R_{xy}}{B} = -\frac{1}{n_s \cdot e}$

And $k_f$ for 2DEG is: 

$k_f  = \sqrt{2 \pi n}$


thus:

$k_f  = \sqrt{\frac{2 \pi}{e R_H  }}$


In [117]:
data_ns = pd.read_excel('data/ns_data.xlsx')
data_ns.drop(data_ns.columns[[3,4,5]], axis=1, inplace = True)
data_ns.columns = ['T', 'Slope Schottky', 'Slope MESA']
data_ns.drop(data_ns.index[0], inplace = True)
#print(data_ns.head())

rH4Kmesa = data_ns.iloc[0]['Slope MESA']
rH6Kmesa = data_ns.iloc[1]['Slope MESA']
rH10Kmesa = data_ns.iloc[2]['Slope MESA']
rH15Kmesa = data_ns.iloc[3]['Slope MESA']


kf4K_hall = np.sqrt(2*scipy.constants.pi/(scipy.constants.e*rH4Kmesa))
print('4K kFermi MESA from Hall is %.3E m^-2' %kf4K_hall) 
kf6K_hall = np.sqrt(2*scipy.constants.pi/(scipy.constants.e*rH6Kmesa))
print('6K kFermi MESA from Hall is %.3E m^-2' %kf6K_hall) 
kf10K_hall = np.sqrt(2*scipy.constants.pi/(scipy.constants.e*rH10Kmesa))
print('10K kFermi MESA from Hall is %.3E m^-2' %kf10K_hall) 
print("\n")

kf4K = np.sqrt(2*scipy.constants.e*frequency4K/scipy.constants.hbar)
print('4K kFermi MESA is %.3E m^-2' %kf4K)    
kf6K = np.sqrt(2*scipy.constants.e*frequency6K/scipy.constants.hbar)
print('6K kFermi MESA is %.3E m^-2' %kf6K)
kf10K = np.sqrt(2*scipy.constants.e*frequency10K/scipy.constants.hbar)
print('10K kFermi MESA is %.3E m^-2' %kf10K)
print("\n")


from tabulate import tabulate

print(tabulate([['4K',kf4K, kf4K_hall], ['6K',kf6K, kf6K_hall], ['10K', kf10K, kf10K_hall]], headers=['temperature', 'sdh', 'hall']))

4K kFermi MESA from Hall is 6.268E+08 m^-2
6K kFermi MESA from Hall is 6.264E+08 m^-2
10K kFermi MESA from Hall is 6.262E+08 m^-2


4K kFermi MESA is 6.236E+08 m^-2
6K kFermi MESA is 6.234E+08 m^-2
10K kFermi MESA is 6.232E+08 m^-2


temperature            sdh         hall
-------------  -----------  -----------
4K             6.23645e+08  6.26818e+08
6K             6.23401e+08  6.26413e+08
10K            6.23157e+08  6.26156e+08


## Finding effective mass 

first we need to detect the peaks and get their coordinates

this thread explains why prominence is a good parameter for finding peaks
- https://stackoverflow.com/questions/1713335/peak-finding-algorithm-for-python-scipy

In [87]:
from scipy.signal import find_peaks

#watch out! the lower the prominence the slower the algorithm works
def peaks_and_valleys(df, prominence_val):
    
    data_x = df['field'].values
    data_y = df['dR/R'].values 
    indices = find_peaks(data_y, prominence = prominence_val)[0]
    valleys = find_peaks(-data_y, prominence = prominence_val)[0]

    fig = go.Figure()
    fig.add_trace(go.Scatter(
        y=data_y,
        mode='lines+markers',
        name='Original Plot'
    ))

    fig.add_trace(go.Scatter(
        x=indices,
        y=[data_y[j] for j in indices],
        mode='markers',
        marker=dict(
            size=8,
            color='red',
            symbol='cross'
        ),
        name='Detected Peaks'
    ))


    fig.add_trace(go.Scatter(
        x=valleys,
        y=[data_y[j] for j in valleys],
        mode='markers',
        marker=dict(
            size=8,
            color='yellow',
            symbol='cross'
        ),
        name='Detected Valleys'
    ))


    fig.update_layout(
        width = 800, height = 600, template = 'simple_white',
        xaxis_title=r'Magnetic field, T',
        yaxis_title=r'Amplitude', font=dict(
            size=18
        ))
    fig.show()
    
peaks_and_valleys(mesa4K,.5)

peaks_and_valleys(mesa6K,.5)
peaks_and_valleys(mesa10K,.1)




In [88]:
peaks_and_valleys(mesa15K,.03)
peaks_and_valleys(mesa20K,.03)

In [29]:
def ift2(df, f1, f2, step):
    dfInt = df.loc[df['field'] >1] 
    n = dfInt.shape[0] #number of points in 'time'
    freq = np.arange(f1, f2, step) #create a set of frequencies
    vals = dfInt['dR/R'].values #values in our fft transform
    times = dfInt['field'].values #'times' in our fft transform
    transform = np.zeros(len(freq),dtype=complex)
    #df['freq'] = freq
    df.loc[:,'freq'] = pd.Series(freq)  #this helps avoiding creating additional data structure. however, the rows don't make much sense anymore. unlucky :(
    for i in range(len(freq)):
        transform[i] = sum(vals[k]*np.exp(-2j*times[k]*np.pi*freq[i]) for k in range(n))/n
    
    df.loc[:,'transform'] = pd.Series(np.absolute(transform))
  
    fig = px.scatter(x=freq, y=np.absolute(transform),width = 1000, height = 800, template = 'simple_white')
    fig.update_layout(
    xaxis_title=r'Magnetic field, T',
    yaxis_title=r'Amplitude', font=dict(
        size=18
    ))
#markers style
    fig.update_traces(marker=dict(size=2,opacity=1, color = "black",
                              line=dict(width=.5,
                                        color="#53868B")),
                  selector=dict(mode='markers'))
    fig.show()


ift2(data4K,0,5,.005)

In [6]:
np.linspace(.11,.25,8)

array([0.11, 0.13, 0.15, 0.17, 0.19, 0.21, 0.23, 0.25])

In [83]:
clear(indexList)

array([1.000e-03, 2.000e-03, 3.000e-03, ..., 9.998e+00, 9.999e+00,
       1.000e+01])

In [171]:
len(xf)

3000

In [114]:
N*T

10.0

In [196]:
mesa4Kresampled.shape[0]

3000